In [1]:
""" mount drive """

import os

GOOGLE_DIR = '/content/drive/My Drive/DL_Project'
LOCAL_DIR = '/home/ziyan/Desktop/Deep Learning Project'

def colab_mount_google_drive():
    drive.mount('/content/drive', force_remount=True)
    os.chdir(GOOGLE_DIR)
    os.listdir()

def mount_local_drive():
    os.chdir(LOCAL_DIR)
    os.listdir()

try:
    from google.colab import drive
    colab_mount_google_drive()
    DIR = GOOGLE_DIR
    print('Mounted google drive')
except ModuleNotFoundError:
    mount_local_drive
    DIR = LOCAL_DIR
    print('Mounted local drive')

Mounted local drive


In [2]:
""" model specification """

# for dataset
product = 'input_df_cross_assets_v2'

fields = [
    'mid_lag_10s', 'mid_lag_30s', 'mid_lag_01m',
    'wmid_ma_05m', 'wmid_ma_10m', 
    'wmid_max_05m', 'wmid_max_10m', 
    'wmid_min_05m', 'wmid_min_10m', 
    'wmid_bidask_01m',
    'total_volume_10s', 'total_volume_01m', 
    'signed_volume_10s', 'signed_volume_01m',
    'signed_tick_10s', 'signed_tick_01m',
    'IF_mid_lag_05s', 'IF_mid_lag_30s',
    'IF_total_volume_10s', 'IF_total_volume_01m',
    'IC_mid_lag_05s', 'IC_mid_lag_30s',
    'IC_total_volume_10s', 'IC_total_volume_01m'
]  # column names
y_field = 'mid_30s'

series_length = 60  # number of samples
sample_interval = 30  # sample every 30 seconds
cache_limit = 300

use_cuda = True

# for train and validate dataloader
params = {
    'batch_size': 1,
    'shuffle': True,
    'num_workers': 3
}

train_sd = '20180102'
train_ed = '20180930'
validate_sd = '20181001'
validate_ed = '20181031'
test_sd = '20181101'
test_ed = '20181231'

In [11]:
import pandas as pd
df1 = pd.read_csv('input_df_cross_assets_v2/input_20181101.csv.gz')
df1[fields].iloc[0]
#df1['mid_lag_30s'].iloc[3565:3580]
# df1.head()

mid_lag_10s              1.400000
mid_lag_30s              2.500000
mid_lag_01m              4.000000
wmid_ma_05m              3.539806
wmid_ma_10m              5.318519
wmid_max_05m            -0.766667
wmid_max_10m            -0.766667
wmid_min_05m             8.600000
wmid_min_10m            12.600000
wmid_bidask_01m       -686.663204
total_volume_10s        16.000000
total_volume_01m        56.000000
signed_volume_10s        2.000000
signed_volume_01m       15.000000
signed_tick_10s          6.000000
signed_tick_01m         13.000000
IF_mid_lag_05s           0.600000
IF_mid_lag_30s           4.100000
IF_total_volume_10s     31.000000
IF_total_volume_01m     88.000000
IC_mid_lag_05s           0.700000
IC_mid_lag_30s          -2.100000
IC_total_volume_10s      6.000000
IC_total_volume_01m     27.000000
Name: 0, dtype: float64

In [3]:
""" create index table for selected product """
import re

os.chdir(os.path.join(DIR, product))
table_file = f'{product}_train_indexes_{series_length}_{sample_interval}.csv'

if not os.path.isfile(table_file):  # skip this step if the index tables already exists (only check train here)
    files = {'train': [], 'validate': [], 'test': []}  # dict of list of dicts
    
    for fn in sorted(os.listdir()):
        # rows number is first subtracted by {series_length} at the begining
        m = re.search('input_(2018\d{4})', fn)
        if m:
            date = m.group(1)
            if date <= train_ed:
                data_type = 'train'
            elif date <= validate_ed:
                data_type = 'validate'
            else:
                data_type = 'test'
            
            df = pd.read_csv(fn)
            cutoff = series_length * sample_interval / 0.5  # drop the tailing indexes
            files[data_type].append({'file_name': fn, 'rows': int(df.shape[0] - cutoff - 1)})

    for data_type in files:
        table = pd.DataFrame(files[data_type])
        table['date'] = table['file_name'].str.split('_').str[-1].str.split('.').str[0]
        table_file = f'{product}_{data_type}_indexes_{series_length}_{sample_interval}.csv'
        table.to_csv(f'{table_file}', index=False)
        print(f'Wrote {data_type} index table to {product}/{table_file}')
else:
    print('Skipped.')

os.chdir(os.path.join(DIR))

Skipped.


In [3]:
""" Create data generators """

from torch.utils import data
from dataset import Dataset

# create a train, validation and test data loader
train_set = Dataset(train_sd, train_ed, product=product, data_type='train', x_fields=fields, y_field=y_field, 
                    series_length=series_length, sample_interval=sample_interval,
                    cache_limit=cache_limit, last_output_only=False)
train_loader = data.DataLoader(train_set, **params)

validation_set = Dataset(validate_sd, validate_ed, product=product, data_type='validate', x_fields=fields, y_field=y_field,
                         series_length=series_length, sample_interval=sample_interval,
                         cache_limit=cache_limit, last_output_only=False)
validation_loader = data.DataLoader(validation_set, **params)

test_set = Dataset(test_sd, test_ed, product=product, data_type='test', x_fields=fields, y_field=y_field,
                   series_length=series_length, sample_interval=sample_interval,
                   cache_limit=cache_limit, last_output_only=False)
# for test only
test_params = {
    'batch_size': 1,
    'shuffle': False,
    'num_workers': 3
}
test_loader = data.DataLoader(test_set, **test_params)

In [0]:
""" 
Init and train model

Main issues:
1. tensor shape for LSTM (3 dimensions with batch as the middle one)
2. model (parameter) and data precision should match by using float()
"""

import gc
import torch.optim as optim
from time import time
from models import *

if use_cuda:
    model = PrototypeModel(input_size=len(fields), num_layers=series_length).float().cuda()  # use float precision instead of double
else:
    model = PrototypeModel(input_size=len(fields), num_layers=series_length).float()

criterion = nn.SmoothL1Loss()

optimizer = optim.SGD(model.parameters(), lr=0.01, momentum=0.6)
model.train()
epoch_error = {}
out = []

for epoch in range(1):
    running_loss = 0.0
    start_time = time()
    epoch_error[epoch] = []
    batch_idx = 0
    
    for data, target in train_loader:
        batch_idx += 1
        optimizer.zero_grad()
#         print(data)
        if use_cuda:
            prediction = model(data.float().cuda())
        else:
            prediction = model(data.float())
        
        if use_cuda:
            loss = criterion(prediction, target.cuda())
        else:
            loss = criterion(prediction, target)
        
        loss.backward()
        optimizer.step()
        
        # print statistics
        running_loss += loss.item()
        cost_time = time() - start_time
#         print(prediction, target)
        print('[epoch: %d, batch:  %5d] target: %6.2f | pred: %6.2f | loss: %.5f  | %.2f' %
              (epoch + 1, batch_idx + 1, target, prediction, running_loss, cost_time))
        
        out.append([float(target), float(prediction)])
        running_loss = 0.0
        start_time = time()
        
        epoch_error[epoch].append(loss)
        
        # Remove this when actually training. 
        # Used to terminate early. 
        if batch_idx > 50000: 
            break
            
#     gc.collect()  # does it help?

In [0]:
"""Local Evaluation / Test"""

import numpy as np

test_mode = True

model.eval()
out = []
# model.cuda()
loader = validation_loader if not test_mode else test_loader

with torch.no_grad():
    mse = []
    batch_idx = 0
    
    for data, target in loader:
        batch_idx += 1
#         print(data, target)
        prediction = model(data.float().cuda())
        
        mse.append(np.square(prediction.cpu() - target))
        if test_mode:
            out.append([float(target), float(prediction)])
        
        if test_mode:
            print('[epoch: %d, batch:  %5d] target: %6.2f | pred: %6.2f' %
                  (epoch + 1, batch_idx + 1, target, prediction))
        # Used to terminate early, remove.
        if batch_idx >= 1000: 
            break

print('MSE: %.2f' % (np.array(mse).mean()))
if test_mode:
    print(out)

In [0]:
for name, param in model.named_parameters():
    if param.requires_grad:
        print(name, param.data)

In [0]:
with open('test result_2.csv', 'w') as f:
    for lst in out:
        f.write(','.join([str(i) for i in lst])+'\n')
        

In [4]:
import torch.optim as optim
from time import time
from models import *


model = LinearRegressionModel(len(fields)).cuda()
criterion = nn.SmoothL1Loss()
optimizer = torch.optim.SGD(model.parameters(), lr = 0.001, momentum=0.6)

batch_idx=0
out=[]
for data, target in train_loader:
        batch_idx += 1
        optimizer.zero_grad()
#         print(data)
        if use_cuda:
            prediction = model(data.float().cuda())
        else:
            prediction = model(data.float())
        
        if use_cuda:
            loss = criterion(prediction, target.float().cuda())
        else:
            loss = criterion(prediction, target.float())
        
        loss.backward()
        optimizer.step()
        # print('target', target)
        # print('pred', prediction)
        # print('loss', loss)

        print('[epoch: %d, batch:  %5d] target: %6.2f | pred: %6.2f | loss: %.5f ' %
              (1, batch_idx + 1, target.mean(), prediction.mean(), loss.mean()))
        
        for i in range(len(target)):
          out.append([float(target[i][0]), float(prediction[i])])
        
        # Remove this when actually training. 
        # Used to terminate early. 
        if batch_idx > 10000: 
            break

/home/ziyan/.local/lib/python3.7/site-packages/torch/nn/modules/loss.py:782: UserWarning: Using a target size (torch.Size([1, 60, 1, 1])) that is different to the input size (torch.Size([60])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.smooth_l1_loss(input, target, reduction=self.reduction)


[epoch: 1, batch:      2] target:  -0.22 | pred:   0.07 | loss: 0.55374 
[epoch: 1, batch:      3] target:   0.01 | pred:   0.07 | loss: 0.31713 
[epoch: 1, batch:      4] target:   0.02 | pred:   0.09 | loss: 0.20906 
[epoch: 1, batch:      5] target:   0.01 | pred:   0.11 | loss: 0.42711 
[epoch: 1, batch:      6] target:   0.00 | pred:   0.19 | loss: 0.62975 
[epoch: 1, batch:      7] target:   0.03 | pred:   0.30 | loss: 0.49058 
[epoch: 1, batch:      8] target:   0.11 | pred:   0.09 | loss: 0.77601 
[epoch: 1, batch:      9] target:   0.00 | pred:   0.18 | loss: 0.98329 
[epoch: 1, batch:     10] target:  -0.03 | pred:   4.06 | loss: 3.79815 
[epoch: 1, batch:     11] target:  -0.16 | pred:  -0.04 | loss: 0.44085 
[epoch: 1, batch:     12] target:  -0.52 | pred:   0.33 | loss: 1.15950 
[epoch: 1, batch:     13] target:  -0.10 | pred:  -0.07 | loss: 0.52820 
[epoch: 1, batch:     14] target:  -0.13 | pred:   0.07 | loss: 0.37560 
[epoch: 1, batch:     15] target:  -0.12 | pred:  -

[epoch: 1, batch:    117] target:   0.17 | pred:   0.19 | loss: 0.68322 
[epoch: 1, batch:    118] target:   0.01 | pred:   0.12 | loss: 0.51533 
[epoch: 1, batch:    119] target:  -0.15 | pred:   0.02 | loss: 0.94322 
[epoch: 1, batch:    120] target:   0.04 | pred:   0.08 | loss: 0.63825 
[epoch: 1, batch:    121] target:   0.18 | pred:   0.11 | loss: 0.59397 
[epoch: 1, batch:    122] target:   0.22 | pred:   0.04 | loss: 0.43567 
[epoch: 1, batch:    123] target:  -0.04 | pred:   0.03 | loss: 0.39194 
[epoch: 1, batch:    124] target:  -0.20 | pred:   0.05 | loss: 0.57673 
[epoch: 1, batch:    125] target:   0.02 | pred:   0.01 | loss: 0.46867 
[epoch: 1, batch:    126] target:   0.09 | pred:   0.25 | loss: 0.87720 
[epoch: 1, batch:    127] target:   0.01 | pred:   0.14 | loss: 0.69589 
[epoch: 1, batch:    128] target:   0.01 | pred:  -0.02 | loss: 0.30320 
[epoch: 1, batch:    129] target:   0.17 | pred:   0.02 | loss: 0.46328 
[epoch: 1, batch:    130] target:   0.21 | pred:   

[epoch: 1, batch:    231] target:  -0.08 | pred:   0.01 | loss: 0.37797 
[epoch: 1, batch:    232] target:   0.11 | pred:   0.66 | loss: 0.83673 
[epoch: 1, batch:    233] target:  -0.16 | pred:   0.02 | loss: 0.80339 
[epoch: 1, batch:    234] target:   0.01 | pred:  -0.11 | loss: 0.21748 
[epoch: 1, batch:    235] target:   0.03 | pred:  -0.20 | loss: 0.44434 
[epoch: 1, batch:    236] target:  -0.02 | pred:   0.02 | loss: 0.79758 
[epoch: 1, batch:    237] target:   0.17 | pred:  -0.05 | loss: 0.57180 
[epoch: 1, batch:    238] target:  -0.05 | pred:  -0.02 | loss: 0.31056 
[epoch: 1, batch:    239] target:  -0.49 | pred:  -0.04 | loss: 0.91774 
[epoch: 1, batch:    240] target:  -0.08 | pred:   0.06 | loss: 0.53263 
[epoch: 1, batch:    241] target:   0.17 | pred:  -0.72 | loss: 0.65599 
[epoch: 1, batch:    242] target:  -0.11 | pred:  -0.06 | loss: 0.51426 
[epoch: 1, batch:    243] target:  -0.12 | pred:  -0.03 | loss: 0.45229 
[epoch: 1, batch:    244] target:  -0.06 | pred:   

[epoch: 1, batch:    346] target:  -0.13 | pred:  -0.06 | loss: 0.27937 
[epoch: 1, batch:    347] target:  -0.08 | pred:  -0.00 | loss: 0.72321 
[epoch: 1, batch:    348] target:  -0.19 | pred:   0.02 | loss: 0.41014 
[epoch: 1, batch:    349] target:  -0.08 | pred:   0.01 | loss: 0.53921 
[epoch: 1, batch:    350] target:  -0.13 | pred:  -0.04 | loss: 0.42440 
[epoch: 1, batch:    351] target:   0.50 | pred:   0.07 | loss: 1.04428 
[epoch: 1, batch:    352] target:  -0.26 | pred:  -0.06 | loss: 0.47557 
[epoch: 1, batch:    353] target:  -0.16 | pred:  -0.11 | loss: 0.30136 
[epoch: 1, batch:    354] target:  -0.13 | pred:  -0.05 | loss: 0.33517 
[epoch: 1, batch:    355] target:  -0.29 | pred:  -0.27 | loss: 1.12616 
[epoch: 1, batch:    356] target:   0.07 | pred:  -0.04 | loss: 0.37581 
[epoch: 1, batch:    357] target:   0.13 | pred:  -0.09 | loss: 0.23039 
[epoch: 1, batch:    358] target:   0.17 | pred:  -0.46 | loss: 0.75538 
[epoch: 1, batch:    359] target:  -0.11 | pred:  -

...

[epoch: 1, batch:   9485] target:   0.02 | pred:  -0.02 | loss: 0.69139 
[epoch: 1, batch:   9486] target:  -0.14 | pred:  -0.08 | loss: 0.29878 
[epoch: 1, batch:   9487] target:   0.15 | pred:  -0.10 | loss: 0.64276 
[epoch: 1, batch:   9488] target:  -0.15 | pred:  -0.03 | loss: 0.31781 
[epoch: 1, batch:   9489] target:   0.01 | pred:  -0.04 | loss: 0.20183 
[epoch: 1, batch:   9490] target:  -0.16 | pred:  -0.04 | loss: 0.81490 
[epoch: 1, batch:   9491] target:   0.00 | pred:  -0.03 | loss: 0.29316 
[epoch: 1, batch:   9492] target:  -0.02 | pred:  -0.05 | loss: 0.41445 
[epoch: 1, batch:   9493] target:   0.07 | pred:  -0.04 | loss: 0.29624 
[epoch: 1, batch:   9494] target:  -0.18 | pred:  -0.06 | loss: 0.50117 
[epoch: 1, batch:   9495] target:  -0.20 | pred:  -0.08 | loss: 0.43551 
[epoch: 1, batch:   9496] target:   0.15 | pred:  -0.03 | loss: 0.71591 
[epoch: 1, batch:   9497] target:   0.10 | pred:  -0.03 | loss: 0.42960 
[epoch: 1, batch:   9498] target:  -0.05 | pred:  -

[epoch: 1, batch:   9602] target:  -0.15 | pred:  -0.04 | loss: 0.62796 
[epoch: 1, batch:   9603] target:  -0.02 | pred:  -0.07 | loss: 0.40192 
[epoch: 1, batch:   9604] target:   0.09 | pred:  -0.02 | loss: 0.34745 
[epoch: 1, batch:   9605] target:   0.24 | pred:  -0.03 | loss: 0.51751 
[epoch: 1, batch:   9606] target:  -0.00 | pred:  -0.04 | loss: 0.46206 
[epoch: 1, batch:   9607] target:  -0.11 | pred:  -0.04 | loss: 0.14102 
[epoch: 1, batch:   9608] target:   0.28 | pred:  -0.02 | loss: 0.62415 
[epoch: 1, batch:   9609] target:  -0.08 | pred:  -0.06 | loss: 0.47578 
[epoch: 1, batch:   9610] target:  -0.05 | pred:  -0.04 | loss: 0.28461 
[epoch: 1, batch:   9611] target:  -0.04 | pred:  -0.03 | loss: 0.47954 
[epoch: 1, batch:   9612] target:   0.09 | pred:  -0.04 | loss: 0.37180 
[epoch: 1, batch:   9613] target:   0.02 | pred:   0.03 | loss: 0.35806 
[epoch: 1, batch:   9614] target:  -0.17 | pred:  -0.04 | loss: 0.61688 
[epoch: 1, batch:   9615] target:  -0.10 | pred:  -

[epoch: 1, batch:   9720] target:   0.13 | pred:  -0.04 | loss: 0.57937 
[epoch: 1, batch:   9721] target:   0.08 | pred:  -0.04 | loss: 0.44039 
[epoch: 1, batch:   9722] target:  -0.14 | pred:  -0.05 | loss: 0.53629 
[epoch: 1, batch:   9723] target:   0.26 | pred:  -0.01 | loss: 0.51062 
[epoch: 1, batch:   9724] target:  -0.12 | pred:  -0.05 | loss: 0.50290 
[epoch: 1, batch:   9725] target:   0.04 | pred:  -0.04 | loss: 0.34290 
[epoch: 1, batch:   9726] target:   0.12 | pred:  -0.04 | loss: 0.37615 
[epoch: 1, batch:   9727] target:  -0.04 | pred:  -0.04 | loss: 0.24250 
[epoch: 1, batch:   9728] target:  -0.28 | pred:  -0.04 | loss: 0.82314 
[epoch: 1, batch:   9729] target:  -0.11 | pred:  -0.07 | loss: 0.38058 
[epoch: 1, batch:   9730] target:   0.15 | pred:  -0.03 | loss: 0.37478 
[epoch: 1, batch:   9731] target:   0.03 | pred:  -0.03 | loss: 0.60448 
[epoch: 1, batch:   9732] target:   0.02 | pred:  -0.05 | loss: 0.51607 
[epoch: 1, batch:   9733] target:   0.33 | pred:  -

[epoch: 1, batch:   9834] target:  -0.17 | pred:  -0.05 | loss: 0.31023 
[epoch: 1, batch:   9835] target:   0.14 | pred:  -0.00 | loss: 0.60804 
[epoch: 1, batch:   9836] target:  -0.02 | pred:  -0.03 | loss: 0.46852 
[epoch: 1, batch:   9837] target:   0.08 | pred:  -0.03 | loss: 0.40282 
[epoch: 1, batch:   9838] target:  -0.21 | pred:   0.03 | loss: 0.50203 
[epoch: 1, batch:   9839] target:  -0.16 | pred:  -0.03 | loss: 0.56949 
[epoch: 1, batch:   9840] target:  -0.03 | pred:  -0.04 | loss: 0.52605 
[epoch: 1, batch:   9841] target:   0.26 | pred:   0.01 | loss: 0.41086 
[epoch: 1, batch:   9842] target:  -0.01 | pred:  -0.02 | loss: 0.48606 
[epoch: 1, batch:   9843] target:  -0.05 | pred:  -0.06 | loss: 0.30617 
[epoch: 1, batch:   9844] target:  -0.09 | pred:  -0.02 | loss: 0.25533 
[epoch: 1, batch:   9845] target:   0.17 | pred:  -0.01 | loss: 0.45827 
[epoch: 1, batch:   9846] target:   0.47 | pred:   0.01 | loss: 0.76882 
[epoch: 1, batch:   9847] target:  -0.27 | pred:  -

[epoch: 1, batch:   9950] target:  -0.02 | pred:  -0.02 | loss: 0.21646 
[epoch: 1, batch:   9951] target:   0.13 | pred:  -0.03 | loss: 0.24027 
[epoch: 1, batch:   9952] target:  -0.08 | pred:  -0.04 | loss: 0.23565 
[epoch: 1, batch:   9953] target:  -0.10 | pred:  -0.03 | loss: 0.22168 
[epoch: 1, batch:   9954] target:  -0.13 | pred:  -0.05 | loss: 0.31828 
[epoch: 1, batch:   9955] target:  -0.14 | pred:  -0.02 | loss: 0.54963 
[epoch: 1, batch:   9956] target:   0.18 | pred:  -0.02 | loss: 1.03711 
[epoch: 1, batch:   9957] target:  -0.02 | pred:  -0.06 | loss: 0.43845 
[epoch: 1, batch:   9958] target:   0.09 | pred:  -0.03 | loss: 0.61807 
[epoch: 1, batch:   9959] target:  -0.05 | pred:  -0.04 | loss: 0.77573 
[epoch: 1, batch:   9960] target:  -0.15 | pred:  -0.08 | loss: 0.90011 
[epoch: 1, batch:   9961] target:  -0.17 | pred:  -0.04 | loss: 0.45959 
[epoch: 1, batch:   9962] target:  -0.26 | pred:  -0.04 | loss: 0.59248 
[epoch: 1, batch:   9963] target:   0.10 | pred:  -

In [0]:
print(len(train_set.x_fields), train_set.sample_interval)

24 30


In [17]:
"""Local Evaluation / Test"""

import numpy as np

test_mode = True

model.eval()
out = []
# model.cuda()
loader = validation_loader if not test_mode else test_loader

with torch.no_grad():
    mse = []
    batch_idx = 0
    
    for data, target in loader:
        batch_idx += 1
        
        prediction = model(data.float().cuda())
        
        for i in range(len(prediction)):
            if test_mode:
                print('[batch:  %5d] target: %6.2f | pred: %6.2f' %
                      (batch_idx, target[0][i][0], prediction[i]))
                out.append([float(target[0][i][0]), float(prediction[i])])
        
            mse.append(np.square(prediction[i].cpu() - target[0][i][0]))
            
        
        # Used to terminate early, remove.
        if batch_idx >= 1000: 
            break

print('MSE: %.2f' % (np.array(mse).mean()))
if test_mode:
    print(out)

[batch:      1] target:  -3.80 | pred:  -0.03
[batch:      1] target:   2.70 | pred:  -0.04
[batch:      1] target:  -1.40 | pred:  -0.02
[batch:      1] target:   0.70 | pred:  -0.03
[batch:      1] target:   0.40 | pred:  -0.02
[batch:      1] target:   0.70 | pred:  -0.05
[batch:      1] target:  -5.20 | pred:  -0.04
[batch:      1] target:  -0.30 | pred:  -0.07
[batch:      1] target:   0.30 | pred:  -0.03
[batch:      1] target:   0.20 | pred:  -0.07
[batch:      1] target:   2.30 | pred:  -0.06
[batch:      1] target:   0.40 | pred:  -0.03
[batch:      1] target:  -3.00 | pred:  -0.04
[batch:      1] target:   0.60 | pred:  -0.05
[batch:      1] target:   1.10 | pred:  -0.06
[batch:      1] target:  -0.60 | pred:  -0.05
[batch:      1] target:  -0.50 | pred:  -0.07
[batch:      1] target:   3.20 | pred:  -0.07
[batch:      1] target:   7.70 | pred:  -0.05
[batch:      1] target:   6.10 | pred:  -0.03
[batch:      1] target:  -1.30 | pred:  -0.02
[batch:      1] target:   3.80 | p

[batch:     14] target:   0.60 | pred:  -0.03
[batch:     14] target:  -3.30 | pred:  -0.04
[batch:     14] target:   2.30 | pred:  -0.03
[batch:     14] target:  -1.50 | pred:  -0.06
[batch:     14] target:   0.60 | pred:  -0.07
[batch:     14] target:  -0.10 | pred:  -0.08
[batch:     14] target:   4.00 | pred:  -0.05
[batch:     14] target:   7.60 | pred:  -0.04
[batch:     14] target:   5.60 | pred:  -0.03
[batch:     14] target:  -1.50 | pred:  -0.03
[batch:     14] target:   1.30 | pred:  -0.05
[batch:     14] target:   0.70 | pred:  -0.04
[batch:     14] target:   1.70 | pred:  -0.03
[batch:     14] target:   0.50 | pred:  -0.01
[batch:     14] target:   1.60 | pred:  -0.02
[batch:     14] target:  -3.00 | pred:   0.01
[batch:     14] target:   0.10 | pred:  -0.03
[batch:     14] target:   1.30 | pred:  -0.06
[batch:     14] target:   3.00 | pred:  -0.03
[batch:     14] target:   1.40 | pred:  -0.02
[batch:     14] target:  -0.10 | pred:  -0.02
[batch:     14] target:  -0.20 | p

[batch:     29] target:  -1.30 | pred:  -0.07
[batch:     29] target:   3.20 | pred:  -0.08
[batch:     29] target:  -2.50 | pred:  -0.05
[batch:     29] target:  -4.00 | pred:  -0.04
[batch:     29] target:  -1.40 | pred:  -0.06
[batch:     29] target:  -0.30 | pred:  -0.06
[batch:     29] target:   0.00 | pred:  -0.08
[batch:     29] target:   0.30 | pred:  -0.04
[batch:     29] target:   2.00 | pred:  -0.06
[batch:     29] target:  -0.70 | pred:  -0.04
[batch:     29] target:   0.90 | pred:  -0.05
[batch:     30] target:  -1.70 | pred:  -0.03
[batch:     30] target:   0.00 | pred:  -0.04
[batch:     30] target:  -0.10 | pred:  -0.05
[batch:     30] target:   2.10 | pred:  -0.04
[batch:     30] target:  -0.10 | pred:  -0.03
[batch:     30] target:  -3.00 | pred:  -0.03
[batch:     30] target:  -2.30 | pred:  -0.06
[batch:     30] target:   0.00 | pred:  -0.04
[batch:     30] target:   0.50 | pred:  -0.04
[batch:     30] target:   2.10 | pred:  -0.05
[batch:     30] target:   0.00 | p

[batch:     44] target:   0.30 | pred:  -0.05
[batch:     44] target:   1.10 | pred:  -0.03
[batch:     44] target:  -1.70 | pred:  -0.05
[batch:     44] target:  -0.30 | pred:  -0.08
[batch:     44] target:  -1.40 | pred:  -0.07
[batch:     44] target:   2.00 | pred:  -0.09
[batch:     44] target:   0.70 | pred:  -0.07
[batch:     44] target:  -2.00 | pred:  -0.06
[batch:     44] target:   0.70 | pred:  -0.08
[batch:     44] target:   1.40 | pred:  -0.04
[batch:     44] target:  -3.50 | pred:  -0.03
[batch:     44] target:  -4.20 | pred:  -0.05
[batch:     44] target:   0.80 | pred:  -0.08
[batch:     44] target:  -2.10 | pred:  -0.05
[batch:     44] target:   1.30 | pred:  -0.08
[batch:     44] target:   0.90 | pred:  -0.04
[batch:     44] target:   1.20 | pred:  -0.04
[batch:     44] target:  -0.30 | pred:  -0.05
[batch:     44] target:  -0.50 | pred:  -0.04
[batch:     45] target:   0.40 | pred:  -0.03
[batch:     45] target:  -0.30 | pred:  -0.03
[batch:     45] target:  -0.70 | p

[batch:     59] target:  -0.20 | pred:  -0.07
[batch:     59] target:   0.10 | pred:  -0.08
[batch:     59] target:   0.60 | pred:  -0.07
[batch:     59] target:   1.00 | pred:  -0.07
[batch:     59] target:  -3.30 | pred:  -0.07
[batch:     59] target:   1.80 | pred:  -0.09
[batch:     59] target:  -0.30 | pred:  -0.05
[batch:     59] target:  -1.70 | pred:  -0.04
[batch:     59] target:  -4.60 | pred:  -0.04
[batch:     59] target:   0.80 | pred:  -0.06
[batch:     59] target:  -3.20 | pred:  -0.07
[batch:     59] target:   1.60 | pred:  -0.10
[batch:     59] target:   1.60 | pred:  -0.06
[batch:     59] target:   1.10 | pred:  -0.05
[batch:     59] target:   0.50 | pred:  -0.05
[batch:     59] target:  -0.70 | pred:  -0.04
[batch:     60] target:   3.50 | pred:  -0.05
[batch:     60] target:  -1.30 | pred:  -0.03
[batch:     60] target:   0.60 | pred:  -0.03
[batch:     60] target:   0.30 | pred:  -0.03
[batch:     60] target:   0.40 | pred:  -0.05
[batch:     60] target:  -4.80 | p

...

[batch:    948] target:  -0.70 | pred:  -0.08
[batch:    948] target:   2.90 | pred:  -0.06
[batch:    948] target:   5.80 | pred:  -0.05
[batch:    948] target:   6.80 | pred:  -0.03
[batch:    948] target:   1.40 | pred:  -0.02
[batch:    948] target:   3.70 | pred:  -0.04
[batch:    948] target:  -3.20 | pred:  -0.03
[batch:    948] target:   4.30 | pred:  -0.04
[batch:    948] target:  -1.40 | pred:  -0.00
[batch:    948] target:  -0.10 | pred:  -0.00
[batch:    948] target:   0.20 | pred:  -0.00
[batch:    948] target:  -2.80 | pred:  -0.02
[batch:    948] target:   3.70 | pred:  -0.03
[batch:    948] target:  -0.80 | pred:  -0.00
[batch:    948] target:   3.10 | pred:  -0.05
[batch:    948] target:   1.90 | pred:  -0.03
[batch:    948] target:  -0.90 | pred:  -0.02
[batch:    948] target:  -0.70 | pred:  -0.05
[batch:    948] target:  -0.30 | pred:  -0.04
[batch:    948] target:  -0.20 | pred:  -0.04
[batch:    948] target:   4.10 | pred:  -0.05
[batch:    948] target:  -1.10 | p

[batch:    962] target:   0.70 | pred:  -0.04
[batch:    962] target:   2.70 | pred:  -0.05
[batch:    962] target:   0.40 | pred:  -0.03
[batch:    962] target:  -0.80 | pred:  -0.04
[batch:    962] target:  -0.10 | pred:  -0.03
[batch:    962] target:  -1.10 | pred:  -0.03
[batch:    962] target:  -0.20 | pred:  -0.04
[batch:    962] target:  -1.10 | pred:  -0.05
[batch:    962] target:   1.30 | pred:  -0.07
[batch:    962] target:  -2.80 | pred:  -0.03
[batch:    963] target:  -0.10 | pred:  -0.08
[batch:    963] target:   2.80 | pred:  -0.06
[batch:    963] target:   7.60 | pred:  -0.05
[batch:    963] target:   6.70 | pred:  -0.03
[batch:    963] target:  -1.70 | pred:  -0.02
[batch:    963] target:   3.50 | pred:  -0.04
[batch:    963] target:  -2.80 | pred:  -0.03
[batch:    963] target:   5.90 | pred:  -0.03
[batch:    963] target:  -2.30 | pred:   0.01
[batch:    963] target:   0.60 | pred:  -0.01
[batch:    963] target:  -1.90 | pred:  -0.00
[batch:    963] target:  -2.10 | p

[batch:    977] target:  -0.60 | pred:  -0.05
[batch:    977] target:   2.10 | pred:  -0.06
[batch:    977] target:   0.80 | pred:  -0.05
[batch:    977] target:  -0.80 | pred:  -0.04
[batch:    977] target:   1.00 | pred:  -0.03
[batch:    977] target:   3.30 | pred:  -0.05
[batch:    977] target:   0.60 | pred:  -0.03
[batch:    977] target:  -0.70 | pred:  -0.03
[batch:    977] target:  -0.90 | pred:  -0.04
[batch:    977] target:   0.50 | pred:  -0.06
[batch:    977] target:  -1.50 | pred:  -0.02
[batch:    977] target:   0.20 | pred:  -0.05
[batch:    977] target:  -0.70 | pred:  -0.05
[batch:    977] target:   0.80 | pred:  -0.07
[batch:    977] target:  -4.20 | pred:  -0.05
[batch:    978] target:   0.10 | pred:  -0.07
[batch:    978] target:   3.70 | pred:  -0.05
[batch:    978] target:   8.30 | pred:  -0.05
[batch:    978] target:   5.40 | pred:  -0.05
[batch:    978] target:  -1.30 | pred:  -0.02
[batch:    978] target:   1.60 | pred:  -0.04
[batch:    978] target:   1.60 | p

[batch:    992] target:   0.10 | pred:  -0.04
[batch:    992] target:  -2.30 | pred:  -0.05
[batch:    992] target:   1.40 | pred:  -0.06
[batch:    992] target:  -1.30 | pred:  -0.03
[batch:    992] target:  -0.30 | pred:  -0.04
[batch:    992] target:   0.10 | pred:  -0.06
[batch:    992] target:  -0.10 | pred:  -0.05
[batch:    992] target:   0.20 | pred:  -0.05
[batch:    992] target:  -4.10 | pred:  -0.05
[batch:    993] target:   2.40 | pred:  -0.08
[batch:    993] target:   3.50 | pred:  -0.05
[batch:    993] target:   8.00 | pred:  -0.06
[batch:    993] target:   2.70 | pred:  -0.02
[batch:    993] target:   1.90 | pred:  -0.04
[batch:    993] target:  -2.90 | pred:  -0.01
[batch:    993] target:   6.20 | pred:  -0.04
[batch:    993] target:  -2.80 | pred:  -0.01
[batch:    993] target:   0.90 | pred:  -0.03
[batch:    993] target:   2.00 | pred:  -0.01
[batch:    993] target:  -4.10 | pred:  -0.01
[batch:    993] target:   1.20 | pred:  -0.03
[batch:    993] target:  -0.20 | p

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [19]:
np.array(mse).mean()

4.959361805032067

In [50]:
import pandas as pd
df=pd.DataFrame(out, columns=['target', 'pred'])

In [23]:
df.head()

target      pred
0    -3.8 -0.026052
1     2.7 -0.043033
2    -1.4 -0.022188
3     0.7 -0.033224
4     0.4 -0.019075

In [55]:
def group_values(x):
    if x >= 0.04:
        return '>0.04'
    if 0.02 > x >= 0:
        return '>0'
    elif 0.04 > x >= 0.02:
        return '<0.02'
    elif x >= -0.02:
        return '>-0.02'
    elif x >= -0.04:
        return '>-0.04'
    else:
        return '<-0.04'

df['target']=df['target'].apply(group_values)
df['pred']=df['pred'].apply(group_values)
print(df.head())

   target    pred
0  <-0.04  >-0.04
1   >0.04  <-0.04
2  <-0.04  >-0.04
3   >0.04  >-0.04
4   >0.04  >-0.02


In [56]:
pd.crosstab([df['target']],
            [df['pred']])

pred    <-0.04  >-0.02  >-0.04   >0
target                             
<-0.04   15725    3305    8188  900
>-0.02     112      51       0    0
>0         779     124     299   16
>0.04    19877    2306    8184  134

In [57]:
len(out)

60000